In [1]:
#Import Libraries
from selenium import webdriver
from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import NoSuchElementException,TimeoutException
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException
import pandas as pd
import lxml
import os
import time
import datetime
import json

In [2]:
#Start Timmer
start = time.time()

#Set Output Folder
output_folder = datetime.datetime.now().strftime("Date-%Y-%m-%d-Time-%H-%M-%S")
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

In [3]:
#Start Chrome
driver = webdriver.Chrome()
driver.implicitly_wait(20) # seconds

#Prepare URL
protocol = "https://"
url = protocol + "rhreporting.nic.in/netiay/PhysicalProgressReport/YearWiseHouseCompletionReport.aspx?"
params = {
    'params': 0
}
for key, value in params.items():
    url = url + "&" + key + "=" + str(value)

#Playing with headers
my_referer = url
UserAgent = 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/39.0.2171.95 Safari/537.36'
mod_headers = {'referer': my_referer, 'User-Agent':UserAgent}

#Start Chrome
driver.get(url)

In [4]:
# Select List
year_select_name = 'ctl00$ContentPlaceHolder1$ddlFinYear'
scheme_select_name = 'ctl00$ContentPlaceHolder1$ddlScheme'
state_select_name = 'ctl00$ContentPlaceHolder1$ddlState'
district_select_name = 'ctl00$ContentPlaceHolder1$ddlDistrict'
block_select_name = 'ctl00$ContentPlaceHolder1$ddlBlock'
submit_button_name = 'ctl00$ContentPlaceHolder1$btnSubmit'
content_table_pane = 'ContentPlaceHolder1_gvDataPanelItem'
content_table_head_id = 'ContentPlaceHolder1_gvDataCopy'
content_table_id = 'ContentPlaceHolder1_gvData'

In [5]:
#Build State List
def build_list(element_name):
    temp_list = driver.find_element_by_name(element_name).find_elements_by_xpath(".//option")[1:]
    _list = []
    #loop over each option
    for x in temp_list:
        d = {}
        d['text'] = x.text
        d['value'] = x.get_attribute('value')
        _list.append(d)
        #print("_list index:",i,d)
    return _list

#Check Submit button
def delete_submit():
    driver.execute_script("return document.getElementsByName('" + submit_button_name + "')[0].remove()")
def check_submit():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, submit_button_name ) ) )

#Check table
def delete_submit():
    driver.execute_script("return document.getElementsByName('" + submit_button_name + "')[0].remove()")
def check_submit():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, submit_button_name ) ) )    
    
#Check submit button
def delete_content():
    driver.execute_script("return document.getElementsByClassName('col-lg-10')[0].remove()")
def check_error():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.ID, "ContentPlaceHolder1_lbl_data_msg" ) ) )
    

In [6]:
def get_total_houselist():
    #Wait for Table to Load fully
    element_present = EC.presence_of_element_located((By.ID, content_table_id))            
    WebDriverWait(driver, 2).until(element_present)
    #Once Loaded Create DataFrame from Table
    html_table = driver.find_element_by_id(content_table_id).get_attribute('outerHTML')
    df = pd.read_html(html_table, skiprows=0, header=0)[0]
    df = df[1:-1]        
    total_houses_completed = list(df[df.columns[-1]])
    return total_houses_completed

In [7]:
#Start Chrome
driver.get(url)

#Year Selection
element = WebDriverWait(driver, 10).until(
    EC.element_to_be_clickable((By.NAME, year_select_name))
)
element.find_element_by_xpath(".//option[@value='0']").click()
yearlist = build_list(year_select_name)[0:1]
for year in yearlist:    
    print("--Scrapping data for Year: ", year['text'])
    year_query = ".//option[@value='" + year['value'] + "']"
    delete_submit()
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(year_query).click()
    check_submit()
    
    #DataStore
    df_list = []
    
    #Scheme Selection
    schemelist = build_list(scheme_select_name)
    for scheme in schemelist:
        print("--//--Scrapping data for scheme: ", scheme['text'])
        scheme_query = ".//option[@value='" + scheme['value'] + "']"
        delete_submit()
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, scheme_select_name))
        )
        element.find_element_by_xpath(scheme_query).click()
        check_submit()
        
        # Delete Content
        delete_content()        
        #Submit button
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, submit_button_name))
        )
        element.click()
        
        #Load Filter List
        state_total_houses_completed = get_total_houselist();
        
        #state Selection
        statelist = build_list(state_select_name)
        for stateindex, state in enumerate(statelist):
            print("--//--//--Scrapping data for state: ", state['text'])
            if state_total_houses_completed[int(stateindex)] > 0:
                state_query = ".//option[@value='" + state['value'] + "']"
                delete_submit()
                element = WebDriverWait(driver, 10).until(
                    EC.element_to_be_clickable((By.NAME, state_select_name))
                )
                element.find_element_by_xpath(state_query).click()
                check_submit()
                
                # Delete Content
                delete_content()        
                #Submit button
                element = WebDriverWait(driver, 10).until(
                    EC.element_to_be_clickable((By.NAME, submit_button_name))
                )
                element.click()

                #Load Filter List
                district_total_houses_completed = get_total_houselist();
         
                #district Selection
                districtlist = build_list(district_select_name)
                for districtindex, district in enumerate(districtlist):
                    print("--//--//--//--Scrapping data for district: ", district['text'])
                    if district_total_houses_completed[int(districtindex)] > 0:
                        district_query = ".//option[@value='" + district['value'] + "']"
                        delete_submit()
                        element = WebDriverWait(driver, 10).until(
                            EC.element_to_be_clickable((By.NAME, district_select_name))
                        )
                        element.find_element_by_xpath(district_query).click()
                        check_submit()
                        
                        # Delete Content
                        delete_content()        
                        #Submit button
                        element = WebDriverWait(driver, 10).until(
                            EC.element_to_be_clickable((By.NAME, submit_button_name))
                        )
                        element.click()

                        #Load Filter List
                        block_total_houses_completed = get_total_houselist();

                        #block Selection
                        blocklist = build_list(block_select_name)
                        for blockindex, block in enumerate(blocklist):
                            print("--//--//--//--//--Scrapping data for block: ", block['text'])
                            if block_total_houses_completed[int(blockindex)] > 0:
                                block_query = ".//option[@value='" + block['value'] + "']"
                                delete_submit()
                                element = WebDriverWait(driver, 10).until(
                                    EC.element_to_be_clickable((By.NAME, block_select_name))
                                )
                                element.find_element_by_xpath(block_query).click()
                                check_submit()

                                # Delete Content
                                delete_content()

                                #Submit button
                                element = WebDriverWait(driver, 10).until(
                                    EC.element_to_be_clickable((By.NAME, submit_button_name))
                                )
                                element.click()

                                try:
                                    #Wait for Table to Load fully
                                    element_present = EC.presence_of_element_located((By.ID, content_table_id))            
                                    WebDriverWait(driver, 2).until(element_present)

                                    #Once Loaded Create DataFrame from Table
                                    #html_head = driver.find_element_by_id(content_table_head_id).get_attribute('outerHTML')
                                    #df = pd.read_html(html_head, skiprows=0)[0]
                                    #table_head = list(df.values[0])
                                    html_table = driver.find_element_by_id(content_table_id).get_attribute('outerHTML')
                                    df = pd.read_html(html_table, skiprows=0, header=0)[0]
                                    df = df[1:-1]
                                    #df.columns = table_head
                                    df['Financial Year'] = year['text']
                                    df['Scheme'] = scheme['text']
                                    df['State Name'] = state['text']
                                    df['District Name'] = district['text']
                                    df['Block Name'] = block['text']
                                    df_list.append(df)
                                except Exception as e:
                                    print("Error while table data |", e)


    #merge all dataframes to master dataframe
    df = pd.concat(df_list)
    df = df.reset_index().drop(columns=['index', '#SNo'])
    df['#SNo'] = df.index + 1
    #Save Scrapped File
    df.to_csv(os.path.join(output_folder, year['text']+'_Scrapped_Data.csv'), encoding='utf-8', index=False)

--Scrapping data for Year:  2010-2011
--//--Scrapping data for scheme:  IAY NEW CONSTRUCTION
--//--//--Scrapping data for state:  ARUNACHAL PRADESH
--//--//--Scrapping data for state:  ASSAM
--//--//--Scrapping data for state:  BIHAR
--//--//--//--Scrapping data for district:  ARARIA
--//--//--//--//--Scrapping data for block:  ARARIA
--//--//--//--//--Scrapping data for block:  BHARGAMA
--//--//--//--//--Scrapping data for block:  FORBESGANJ
--//--//--//--//--Scrapping data for block:  JOKIHAT
--//--//--//--//--Scrapping data for block:  KURSAKANTA
--//--//--//--//--Scrapping data for block:  NARPATGANJ
--//--//--//--//--Scrapping data for block:  PALASI
--//--//--//--//--Scrapping data for block:  RANIGANJ
--//--//--//--//--Scrapping data for block:  SIKTY
--//--//--//--Scrapping data for district:  ARWAL
--//--//--//--//--Scrapping data for block:  ARWAL
--//--//--//--//--Scrapping data for block:  KALER
--//--//--//--//--Scrapping data for block:  KARPI
--//--//--//--//--Scrapping 

--//--//--//--//--Scrapping data for block:  BARAULI
--//--//--//--//--Scrapping data for block:  BHOREY
--//--//--//--//--Scrapping data for block:  BIJAIPUR
--//--//--//--//--Scrapping data for block:  GOPALGANJ
--//--//--//--//--Scrapping data for block:  HATHUA
--//--//--//--//--Scrapping data for block:  KATAIYA
--//--//--//--//--Scrapping data for block:  KUCHAIKOTE
--//--//--//--//--Scrapping data for block:  MANJHA
--//--//--//--//--Scrapping data for block:  PANCHDEORI
--//--//--//--//--Scrapping data for block:  PHULWARIYA
--//--//--//--//--Scrapping data for block:  SIDHWALIA
--//--//--//--//--Scrapping data for block:  THAWE
--//--//--//--//--Scrapping data for block:  UCHKAGAON
--//--//--//--Scrapping data for district:  JAMUI
--//--//--//--//--Scrapping data for block:  BARHAT
--//--//--//--//--Scrapping data for block:  CHAKAI
--//--//--//--//--Scrapping data for block:  GIDHOR
--//--//--//--//--Scrapping data for block:  ISLAMNAGAR ALIGANJ
--//--//--//--//--Scrapping da

--//--//--//--//--Scrapping data for block:  BIND BLOCK
--//--//--//--//--Scrapping data for block:  CHANDI BLOCK
--//--//--//--//--Scrapping data for block:  EKANGARSARAI
--//--//--//--//--Scrapping data for block:  GIRIYAK
--//--//--//--//--Scrapping data for block:  HARNAUT BLOCK
--//--//--//--//--Scrapping data for block:  HILSA
--//--//--//--//--Scrapping data for block:  ISLAMPUR  BLOCK
--//--//--//--//--Scrapping data for block:  KARAIPARSURAI
--//--//--//--//--Scrapping data for block:  KATRISARAI
--//--//--//--//--Scrapping data for block:  NAGARNAUSA
--//--//--//--//--Scrapping data for block:  NOORSARAI
--//--//--//--//--Scrapping data for block:  PARWALPUR
--//--//--//--//--Scrapping data for block:  RAHUI BLOCK
--//--//--//--//--Scrapping data for block:  RAJGIR BLOCK
--//--//--//--//--Scrapping data for block:  SARMERA BLOCK
--//--//--//--//--Scrapping data for block:  SILAO BLOCK
--//--//--//--//--Scrapping data for block:  THARTHARI BLOCK
--//--//--//--Scrapping data fo

--//--//--//--//--Scrapping data for block:  BITHAN
--//--//--//--//--Scrapping data for block:  BUBHUTIPUR
--//--//--//--//--Scrapping data for block:  DALSING SARAI
--//--//--//--//--Scrapping data for block:  HASANPURA
--//--//--//--//--Scrapping data for block:  KHANPUR
--//--//--//--//--Scrapping data for block:  KLAYANPUR
--//--//--//--//--Scrapping data for block:  MOHAN PUR
--//--//--//--//--Scrapping data for block:  MOHIUDDIN NAGAR
--//--//--//--//--Scrapping data for block:  MORWA
--//--//--//--//--Scrapping data for block:  PATORI
--//--//--//--//--Scrapping data for block:  PUSA
--//--//--//--//--Scrapping data for block:  ROSRA
--//--//--//--//--Scrapping data for block:  SARAIRANJAN
--//--//--//--//--Scrapping data for block:  SINGHIA
--//--//--//--//--Scrapping data for block:  SIVAJEE NAGAR
--//--//--//--//--Scrapping data for block:  SMASTIPUR
--//--//--//--//--Scrapping data for block:  TAJPUR
--//--//--//--//--Scrapping data for block:  UJIYARPUR
--//--//--//--//--S

--//--//--//--//--Scrapping data for block:  AMBIKAPUR
--//--//--//--//--Scrapping data for block:  BATAULI
--//--//--//--//--Scrapping data for block:  LAKHANPUR
--//--//--//--//--Scrapping data for block:  LUNDRA
--//--//--//--//--Scrapping data for block:  MAINPAT
--//--//--//--//--Scrapping data for block:  SITAPUR
--//--//--//--//--Scrapping data for block:  UDAIPUR
--//--//--Scrapping data for state:  GOA
--//--//--Scrapping data for state:  GUJARAT
--//--//--//--Scrapping data for district:  AHMADABAD
--//--//--//--Scrapping data for district:  AMRELI
--//--//--//--Scrapping data for district:  ANAND
--//--//--//--Scrapping data for district:  ARVALLI
--//--//--//--Scrapping data for district:  BANAS KANTHA
--//--//--//--//--Scrapping data for block:  AMIRGADH
--//--//--//--//--Scrapping data for block:  BHABHAR
--//--//--//--//--Scrapping data for block:  DANTA
--//--//--//--//--Scrapping data for block:  DANTIVADA
--//--//--//--//--Scrapping data for block:  DEESA 
--//--//--/

...

--//--//--Scrapping data for state:  ARUNACHAL PRADESH
--//--//--Scrapping data for state:  ASSAM
--//--//--Scrapping data for state:  BIHAR
--//--//--Scrapping data for state:  CHHATTISGARH
--//--//--Scrapping data for state:  GOA
--//--//--Scrapping data for state:  GUJARAT
--//--//--Scrapping data for state:  HARYANA
--//--//--Scrapping data for state:  HIMACHAL PRADESH
--//--//--Scrapping data for state:  JAMMU AND KASHMIR
--//--//--Scrapping data for state:  JHARKHAND
--//--//--Scrapping data for state:  KERALA
--//--//--Scrapping data for state:  MADHYA PRADESH
--//--//--Scrapping data for state:  MAHARASHTRA
--//--//--Scrapping data for state:  MANIPUR
--//--//--Scrapping data for state:  MEGHALAYA
--//--//--Scrapping data for state:  MIZORAM
--//--//--Scrapping data for state:  NAGALAND
--//--//--Scrapping data for state:  ODISHA
--//--//--Scrapping data for state:  PUNJAB
--//--//--Scrapping data for state:  RAJASTHAN
--//--//--Scrapping data for state:  SIKKIM
--//--//--Scrap

--//--//--Scrapping data for state:  ARUNACHAL PRADESH
--//--//--Scrapping data for state:  ASSAM
--//--//--Scrapping data for state:  BIHAR
--//--//--//--Scrapping data for district:  ARARIA
--//--//--//--Scrapping data for district:  ARWAL
--//--//--//--Scrapping data for district:  AURANAGABAD
--//--//--//--//--Scrapping data for block:  AURANGABAD
--//--//--//--//--Scrapping data for block:  BARUN
--//--//--//--//--Scrapping data for block:  DAUDNAGAR
--//--//--//--//--Scrapping data for block:  DEO
--//--//--//--//--Scrapping data for block:  GOH
--//--//--//--//--Scrapping data for block:  HASPURA
--//--//--//--//--Scrapping data for block:  KUTUMBA
--//--//--//--//--Scrapping data for block:  MADANPUR
--//--//--//--//--Scrapping data for block:  NAWINAGAR
--//--//--//--//--Scrapping data for block:  OBRA
--//--//--//--//--Scrapping data for block:  RAFIGANJ
--//--//--//--Scrapping data for district:  BANKA 
--//--//--//--Scrapping data for district:  BEGUSARAI
--//--//--//--//--

--//--//--//--//--Scrapping data for block:  MURHU
--//--//--//--//--Scrapping data for block:  RANIA
--//--//--//--//--Scrapping data for block:  TORPA
--//--//--//--Scrapping data for district:  KODERMA
--//--//--//--Scrapping data for district:  LATEHAR
--//--//--//--Scrapping data for district:  LOHARDAGA
--//--//--//--Scrapping data for district:  PAKUR
--//--//--//--Scrapping data for district:  PALAMU
--//--//--//--Scrapping data for district:  RAMGARH
--//--//--//--Scrapping data for district:  RANCHI
--//--//--//--Scrapping data for district:  SAHEBGANJ
--//--//--//--Scrapping data for district:  SARAIKELA KHARSAWAN
--//--//--//--Scrapping data for district:  SIMDEGA
--//--//--//--Scrapping data for district:  WEST SINGHBHUM
--//--//--Scrapping data for state:  KERALA
--//--//--Scrapping data for state:  MADHYA PRADESH
--//--//--//--Scrapping data for district:  AGAR-MALWA
--//--//--//--Scrapping data for district:  ALIRAJPUR
--//--//--//--Scrapping data for district:  ANUPPUR

--//--//--Scrapping data for state:  ARUNACHAL PRADESH
--//--//--Scrapping data for state:  ASSAM
--//--//--Scrapping data for state:  BIHAR
--//--//--Scrapping data for state:  CHHATTISGARH
--//--//--Scrapping data for state:  GOA
--//--//--Scrapping data for state:  GUJARAT
--//--//--Scrapping data for state:  HARYANA
--//--//--Scrapping data for state:  HIMACHAL PRADESH
--//--//--Scrapping data for state:  JAMMU AND KASHMIR
--//--//--Scrapping data for state:  JHARKHAND
--//--//--Scrapping data for state:  KERALA
--//--//--Scrapping data for state:  MADHYA PRADESH
--//--//--Scrapping data for state:  MAHARASHTRA
--//--//--Scrapping data for state:  MANIPUR
--//--//--Scrapping data for state:  MEGHALAYA
--//--//--Scrapping data for state:  MIZORAM
--//--//--Scrapping data for state:  NAGALAND
--//--//--Scrapping data for state:  ODISHA
--//--//--Scrapping data for state:  PUNJAB
--//--//--Scrapping data for state:  RAJASTHAN
--//--//--Scrapping data for state:  SIKKIM
--//--//--Scrap

--//--//--//--//--Scrapping data for block:  AHMEDGARH
--//--//--//--//--Scrapping data for block:  ANDANA
--//--//--//--//--Scrapping data for block:  BHAWANIGARH
--//--//--//--//--Scrapping data for block:  DHURI
--//--//--//--//--Scrapping data for block:  DIRBA
--//--//--//--//--Scrapping data for block:  LEHRAGAGA
--//--//--//--//--Scrapping data for block:  MALERKOTLA
--//--//--//--//--Scrapping data for block:  SANGRUR
--//--//--//--//--Scrapping data for block:  SHERPUR
--//--//--//--//--Scrapping data for block:  SUNAM
--//--//--//--Scrapping data for district:  SAS NAGAR
--//--//--//--Scrapping data for district:  TARAN TARAN
--//--//--Scrapping data for state:  RAJASTHAN
--//--//--Scrapping data for state:  SIKKIM
--//--//--Scrapping data for state:  TAMIL NADU
--//--//--Scrapping data for state:  TRIPURA
--//--//--Scrapping data for state:  UTTAR PRADESH
--//--//--Scrapping data for state:  UTTARAKHAND
--//--//--Scrapping data for state:  WEST BENGAL
--//--//--Scrapping dat

In [45]:
df = pd.concat(df_list)

In [8]:
df

Panchayat Name  Houses completed for prior to 2005-2006  \
0             Araria Basti Panchayat                                        0   
1                  Bangama Panchayat                                        0   
2                 Bansbari Panchayat                                        0   
3                Basantpur Panchayat                                        0   
4                Baturbari Panchayat                                        0   
5                    Belwa Panchayat                                        0   
6                    Bochi Panchayat                                        0   
7               Chandardei Panchayat                                        0   
8                   Chatar Panchayat                                        0   
9                   Chikni Panchayat                                        0   
10                  Diyari Panchayat                                        0   
11                   Gaira Panchayat                                        0   
12                 Gaiyari Panchayat                                        0   
13                  Hariya Panchayat                                        0   
14                Hayatpur Panchayat                                        0   
15                   Jamua Panchayat                                        0   
16                  Jhamta Panchayat                                        0   
17               Kamaldaha Panchayat                                        0   
18        Kismat Khawaspur Panchayat                                        0   
19             Kusiyargaon Panchayat                                        0   
20            Madanpur (E) Panchayat                                        0   
21            Madanpur (W) Panchayat                                        0   
22                Paiktola Panchayat                                        0   
23               Pakhariya Panchayat                                        0   
24       Rampur Kodarkatti Panchayat                                        0   
25     Rampur Mohanpur (E) Panchayat                                        0   
26     Rampur Mohanpur (W) Panchayat                                        0   
27                Sahasmal Panchayat                                        0   
28               Sharanpur Panchayat                                        0   
29         Tatouna Bhojpur Panchayat                                        0   
...                              ...                                      ...   
45939                   MAHOLI KALAN                                        0   
45940                   MAHOLI KHURD                                        0   
45941       MALAKPUR (JANDALI KHURD)                                        0   
45942                      MANAKHERI                                        0   
45943                         MANAKI                                        0   
45944                          MATOI                                        0   
45945    MEHBOOBPURA ( TAKHAR KHURD)                                        0   
45946                       MITHEWAL                                        0   
45947                       MOMNABAD                                        0   
45948           MUBARAKPUR (CHUNGHA)                                        0   
45949                      NAROMAZRA                                        0   
45950                     NATHO HERI                                        0   
45951                    NATHU MAJRA                                        0   
45952                     NAUDHARANI                                        0   
45953                      RASOOLPUR                                        0   
45954                         ROHIRA                                        0   
45955                          RURKA                                        0   
45956                       SADATPUR                 